In [2]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py


SRP_name = 'aggregates'
resolution = '1kbp_raw' 
species= 'mouse'


def calc_auroc (df_trial,predicted_score='predicted_score'):
    df_trial = df_trial.sort_values(by=[predicted_score], ascending=False)
    rank_abs = lambda x: stats.rankdata(x)
    predicts2 = np.apply_along_axis(rank_abs, 0, df_trial[predicted_score].values)
    df_trial['p'] = [y if x==1 else 0 for x,y in zip(df_trial['true_pos'], predicts2)]
    #print (df_trial['p'].sum())
    if df_trial['true_neg'].sum() == 0 or df_trial['true_pos'].sum() == 0:
        return np.nan
    else:
        return (((df_trial['p'].sum() /df_trial['true_pos'].sum() )- (df_trial['true_pos'].sum() + 1)/2)) / df_trial['true_neg'].sum()


exp_file_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/spr/hic_gene_corr_inter_excluding_intra_chrom_pairs_hicexp.h5'
jac_sim_spr = hm.hiCMatrix(exp_file_path)
all_genes_spr = [x[3].decode() for x in jac_sim_spr.cut_intervals]
df_jac_corr = pd.DataFrame(jac_sim_spr.matrix.toarray() ,  index=all_genes_spr, columns = all_genes_spr)
  

input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
bins_bed['bin_id'] = bins_bed.index
  
chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()
chrom_index_list = {}
for chrom in chr_list:
      st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
      en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
      chrom_index_list[chrom] = list(range(st, en+1))
gene_bed = pd.read_csv(f'{input_path}/all_gene.bed', names=['chr', 'start_bin', 'end_bin', 'gene'])



marker_list = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_cluster_markers.csv')

all_markers_df = []
for marker_type in ['class', 'subclass', 'cluster']:
	marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_type}_markers.csv')
	all_markers_df.append(marker_list)

marker_list = pd.concat(all_markers_df)
marker_list = marker_list.drop_duplicates(subset=['gene'])
df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
#df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 
#df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
#marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
#marker_list = marker_list.drop_duplicates(subset=['Ensembl_gene_identifier'])
marker_list = marker_list.drop_duplicates(subset=['gene_id'])

with h5py.File(f'{input_path}/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
        tot_g = (list(hf.keys()))

all_background_markers = list(set(all_genes_spr) -  set(marker_list['gene_id'].tolist())) + marker_list['gene_id'].tolist()
all_background_markers = list(set(marker_list['gene_id'].tolist()))


marker_contacts_list_inter = []

gene_list = []
with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
                   
                   for key in all_background_markers:
                    if key in tot_g:
                            gene_list.append(key)
                            gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                            #which ever chrom the gene falls into, those bins should be nan
                            my_data = hf[key][()]
                            my_data = my_data.astype('float32')
                            my_data[chrom_index_list[gene_chrom]] = np.nan
                            marker_contacts_list_inter.append(my_data)
                            
                            
my_data = np.array(marker_contacts_list_inter)

df_max_gene_inter_by_bins = pd.DataFrame(my_data, index=gene_list, columns = bins_bed['bin_id'].tolist())

df_max_gene_inter_by_bins_normalized = df_max_gene_inter_by_bins.div(df_max_gene_inter_by_bins.mean(axis=1, skipna=True), axis=0)
df_max_gene_inter_by_bins = df_max_gene_inter_by_bins_normalized

#df_max_gene_inter_by_bins_sum = df_max_gene_inter_by_bins.sum().reset_index()

#df_max_gene_inter_by_bins_sum_mean = df_max_gene_inter_by_bins.mean().reset_index()



INFO:numexpr.utils:Note: detected 192 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 192 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.
/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (15,16) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


In [3]:
import os
from scipy.stats import mannwhitneyu

number_of_genes_list = [1]
marker_level_list = ['class']

for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        marker_list = marker_list[marker_list['gene_id'].isin(all_genes_spr)]
        #marker_list = marker_list[marker_list['rank'] < number_of_genes]
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
        df2_list = []
                    

                
        for group2 in all_cell_types:
                df2_list.append(marker_list[marker_list['cell_type']==group2].sort_values(by=['rank']).head(number_of_genes))

        marker_list=pd.concat(df2_list)

        marker_table = marker_list.pivot_table(index='gene_id', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)
                    
        marker_table[marker_table != 0] = 1

        all_markers = marker_table.index.tolist()
        

In [3]:
marker_list

group      cell_type  rank    gene  recurrence     auroc  fold_change  \
0      all      GABAergic     1    Gad1           7  0.941159   116.960472   
752    all   Non-Neuronal     1      Qk           7  0.896552    17.743711   
1101   all  Glutamatergic     1  Arpp21           7  0.975092     9.088639   

      fold_change_detection   expression  precision  ...  population_size  \
0                  9.289078   820.463486   0.659089  ...     10207.000000   
752                1.622649  1620.810999   0.086534  ...      8908.857143   
1101               2.043554  1381.680094   0.857382  ...     49843.000000   

      n_datasets  scSS  snSS  scCv2  snCv2  snCv3M  scCv3  snCv3Z  \
0              7  True  True   True   True    True   True    True   
752            7  True  True   True   True    True   True    True   
1101           7  True  True   True   True    True   True    True   

                 gene_id  
0     ENSMUSG00000070880  
752   ENSMUSG00000062078  
1101  ENSMUSG00000032503  

[3 rows x 21 columns]

In [53]:
df_tmp = df_max_gene_inter_by_bins.T

In [7]:
df_tmp

ENSMUSG00000024045  ENSMUSG00000020698  ENSMUSG00000024002  \
0                 0.0                 0.0                 0.0   
1                 0.0                 0.0                 0.0   
2                 0.0                 0.0                 0.0   
3                 0.0                 0.0                 0.0   
4                 0.0                 0.0                 0.0   

   ENSMUSG00000033819  ENSMUSG00000097785  ENSMUSG00000071424  \
0                 0.0                 0.0                 0.0   
1                 0.0                 0.0                 0.0   
2                 0.0                 0.0                 0.0   
3                 0.0                 0.0                 0.0   
4                 0.0                 0.0                 0.0   

   ENSMUSG00000110862  ENSMUSG00000029177  ENSMUSG00000028224  \
0                 0.0                 0.0                 0.0   
1                 0.0                 0.0                 0.0   
2                 0.0                 0.0                 0.0   
3                 0.0                 0.0                 0.0   
4                 0.0                 0.0                 0.0   

   ENSMUSG00000020696  ...  ENSMUSG00000020814  ENSMUSG00000031728  \
0                 0.0  ...                 0.0                 0.0   
1                 0.0  ...                 0.0                 0.0   
2                 0.0  ...                 0.0                 0.0   
3                 0.0  ...                 0.0                 0.0   
4                 0.0  ...                 0.0                 0.0   

   ENSMUSG00000035078  ENSMUSG00000006021  ENSMUSG00000018379  \
0                 0.0                 0.0                 0.0   
1                 0.0                 0.0                 0.0   
2                 0.0                 0.0                 0.0   
3                 0.0                 0.0                 0.0   
4                 0.0                 0.0                 0.0   

   ENSMUSG00000042870  ENSMUSG00000019863  ENSMUSG00000029310  \
0                 0.0                 0.0                 0.0   
1                 0.0                 0.0                 0.0   
2                 0.0                 0.0                 0.0   
3                 0.0                 0.0                 0.0   
4                 0.0                 0.0                 0.0   

   ENSMUSG00000022559  ENSMUSG00000018849  
0                 0.0                 0.0  
1                 0.0                 0.0  
2                 0.0                 0.0  
3                 0.0                 0.0  
4                 0.0                 0.0  

[5 rows x 11023 columns]

In [4]:
#df_max_gene_inter_by_bins_background = df_max_gene_inter_by_bins.T
#df_max_gene_inter_by_bins_background['raw']=df_max_gene_inter_by_bins_background.values.tolist()
df_max_gene_inter_by_bins_background = df_max_gene_inter_by_bins.T.apply(lambda x: x.tolist(), axis=1).reset_index()

In [46]:
df_max_gene_inter_by_bins.head(1000000)[0].max()

0.0

In [5]:
df_max_gene_inter_by_bins_background

index                                                  0
0              0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1              1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2              2  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3              3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4              4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
...          ...                                                ...
2462750  2462750  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462751  2462751  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462752  2462752  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462753  2462753  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462754  2462754  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...

[2462755 rows x 2 columns]

In [50]:
def func(x, y):
    try:
        df = pd.DataFrame(y)
        #print (df.max())
        #print (x, y.dropna())
        U, p_val = mannwhitneyu([x], df.dropna()[0].tolist(), alternative="greater")
        return (p_val)
    except:
        return 2
func2=np.vectorize(func)

In [54]:
test_val = func2(df_tmp['ENSMUSG00000070880'], df_max_gene_inter_by_bins_background[0])

In [51]:
df_max_gene_inter_by_bins_background[0]

0          [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1          [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2          [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3          [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4          [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
                                 ...                        
2462750    [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462751    [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462752    [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462753    [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462754    [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
Name: 0, Length: 2462755, dtype: object

In [18]:
df = pd.DataFrame (df_max_gene_inter_by_bins_background.head()[0][0])
df.dropna()[0].tolist()

In [21]:
df_max_gene_inter_by_bins_background

index                                                  0
0              0  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
1              1  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
2              2  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
3              3  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
4              4  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...
...          ...                                                ...
2462750  2462750  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462751  2462751  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462752  2462752  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462753  2462753  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...
2462754  2462754  [0.0, 0.0, 0.0, 0.0, nan, 0.0, 0.0, 0.0, 0.0, ...

[2462755 rows x 2 columns]

[0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0,
 0.0

In [ ]:
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        df_list_mean = []

        cell_type_list_order = []
        
        df_list_p_val = []

        for group, cell_type in zip(marker_list_groups, marker_list_types):
            
            
            marker_genes_group = marker_table[marker_table[cell_type] == 1].index.tolist()

            df_max_gene_whole_group_1 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]
            df_max_gene_whole_group_2 = df_max_gene_inter_by_bins.loc[:, :]
            

In [ ]:
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        df_list_mean = []

        cell_type_list_order = []
        
        df_list_p_val = []

        for group, cell_type in zip(marker_list_groups, marker_list_types):
            
            
            marker_genes_group = marker_table[marker_table[cell_type] == 1].index.tolist()

            df_max_gene_whole_group_1 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]
            df_max_gene_whole_group_2 = df_max_gene_inter_by_bins.loc[:, :]
            
            def addData(x):
                try:
                    U, p_val = mannwhitneyu(x.dropna().tolist(), df_max_gene_whole_group_2[x.name].dropna().tolist(), alternative="two-sided")
                    return p_val
                except:
                    return np.nan

            
            new_df = df_max_gene_whole_group_1.apply(addData)
            df_list_p_val.append(new_df)
            cell_type_list_order.append(cell_type)
            column_list = df_max_gene_whole_group_1.columns.tolist()
            j = new_df.to_numpy()
            cell_type_name = cell_type.replace('/', "_")
            

/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/scipy/stats/stats.py:7171: RuntimeWarning: divide by zero encountered in double_scalars
  z = (bigu - meanrank) / sd
